In [5]:
import pandas as pd
from geopy.geocoders import Nominatim
#Importación del módulo csv que necesitaremos para leer y escribir en nuestros csv
import csv
#Importación del módulo shutil que usaremos para crear una copia de nuestro csv original
import shutil
import geopandas as gpd
import matplotlib.pyplot as plt
import networkx as nx
import osmnx as ox
import pyrematch as re
from shapely.geometry import shape
import numpy as np
import networkx as nx
from time import time 
from pyproj import CRS
from collections import OrderedDict
import operator
from functools import reduce


# Insertar costos a los arcos de Santiago

**Creamos el grafo de Santiago**

In [6]:
place_name = "Provincia de Santiago, Región Metropolitana de Santiago, Chile"
graph = ox.graph_from_place(place_name, network_type = "drive", simplify = False)

In [7]:
ox.speed.add_edge_speeds(graph, hwy_speeds=None, fallback=None, precision=1)

**Obtenemos los df de nodos y arcos**

In [8]:
nodes, edges = ox.graph_to_gdfs(graph)

In [64]:
nodes[nodes['osmid'] == 1882519127]['y'].values[0]

-33.3226414

**Agregamos columna de tiempo de viaje**

In [9]:
edges['Tiempos de Viaje'] = 0
edges['Tiempos de Viaje'] = edges.apply(lambda x: ((edges['length']/1000)/edges['speed_kph'])) #horas

**Creamos función que disminuirá la velocidad  del los arcos, dependiendo de la hora y minuto del día**

**Funciones que servirán para dar efecto congestión**

In [10]:
def interpolacion_lineal(x,x1,x2,y1,y2):
    y = ((y2-y1)/(x2-x1))*(x-x1)+y1
    return(y)

In [11]:
def interpolacion_cuadratica(x, fx):
    b0 = fx[0]
    b1 = (fx[1]-fx[0])/(x[1]-x[0])
    b2 = (((fx[2]-fx[1])/(x[2]-x[1]))-((fx[1]-fx[0])/(x[1]-x[0])))/(x[2]-x[0])
    f2 = b0+b1*(x[3]-x[0])+b2*(x[3]-x[0])*(x[3]-x[1])
    return(f2)

**Función tiempo final aplicada a la red**

In [12]:
def actualizar_tiempo(x, y, mes, hora, minutos): #x es velocidad e y es distancia
    y = y/1000
    dic_dism = {1:[(20.19/43.15),((20.19+14.09)/43.15),(18.51/43.15)],2:[(21.03/43.15),((21.03+14.09)/43.15),(19.14/43.15)], 3:[(16.89/43.15),((16.89+14.09)/43.15),(17.39/43.15)], 4:[(16.93/43.15),((16.93+14.09)/43.15),(17.38/43.15)], 5:[(17.19/43.15),((17.19+14.09)/43.15),(17.17/43.15)], 6:[(17.34/43.15),((17.34+14.09)/43.15),(17.08/43.15)], 7:[(18.46/43.15),((18.46+14.09)/43.15),(17.21/43.15)], 8:[(16.76/43.15),((16.76+14.09)/43.15),(16.94/43.15)], 9:[(17.15/43.15),((17.15+14.09)/43.15),(17.24/43.15)], 10:[(16.78/43.15),((16.78+14.09)/43.15),(17.02/43.15)], 11:[(16.57/43.15),((16.57+14.09)/43.15),(17.03/43.15)], 12:[(18.11/43.15),((18.11+14.09)/43.15),(17.13/43.15)]}
    #Punta mañana [0], Valle [1], Punta Tarde [2]
    if ((7 <= hora <= 8) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([5, 8, 10.5, (hora+(minutos/60))], [x, x*dic_dism[mes][0], interpolacion_lineal(10.5,8,13.5,x*dic_dism[mes][0],x*dic_dism[mes][1])])
    elif ((9 <= hora <= 17) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([10.5, 13.5, 16.25,(hora +(minutos/60))],[interpolacion_lineal(10.5,8,13.5,x*dic_dism[mes][0],x*dic_dism[mes][1]),x*dic_dism[mes][1], interpolacion_lineal(16.25,13.5,19,x*dic_dism[mes][1],x*dic_dism[mes][2])])
    elif ((18 <= hora <= 19) and (0 <= minutos <= 59)):
        x = interpolacion_cuadratica([16.25, 19, 22, (hora+(minutos/60))],[interpolacion_lineal(16.25,13.5,19,x*dic_dism[mes][1],x*dic_dism[mes][2]),x*dic_dism[mes][2],x])
    return (y/x) #horas

**Ahora probamos la función para los diferentes horarios**

00:03 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

8:33 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

10:32 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

13:00 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

13:30 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

18:20 hrs.

In [ ]:
#nodes, edges = ox.graph_to_gdfs(graph)

In [ ]:
#actualizar_tiempo(x, y, mes, hora, minutos)
#edges['Tiempo de Viaje'][10:20]

**Función Dijsktra dependiente del tiempo**

In [13]:
def subgrafo(graph, src, direccion_x, direccion_y, m, n):
    subgrafo = nx.ego_graph(graph, src, radius = (ox.distance.great_circle_vec(direccion_x[m], direccion_y[m], direccion_x[n], direccion_y[n], earth_radius = 6371009)/100)+210, center=True, undirected=False, distance=None)
    return subgrafo

In [14]:
from heapq import *
def dijkstra_tiempo(graph, src, dest, mes, hora, minutos, visited = set(), times={}, predecessors={}):
    
    """ calculates a shortest path tree routed in src
    """    
    if src == dest:
        #print('LLEGÓ AL DESTINO------------------')
        # We build the shortest path and display it
        path=[]
        pred=dest
        while pred != None:
            path.append(pred)
            pred=predecessors.get(pred,None)
        # reverses the array, to display the path nicely
        readable=path[0]

        return(path, times[dest])
        
    else : 
        # if it is the initial  run, initializes the cost
        if not visited: 
            times[src] = 0
            
        #print('SRC', src)
        #print('graph', graph)
        for neighbor in graph[src] :
            print('neighbor', neighbor)
            print('visited', visited)
            if neighbor not in visited:
                x = graph[src][neighbor][0]['speed_kph']
                y = graph[src][neighbor][0]['length']
                act_time = actualizar_tiempo(x, y, mes, hora, minutos) #horas
                new_time = times[src] + act_time # tiempo acumulado en horas
                if new_time < times.get(neighbor,float('inf')):
                    times[neighbor] = new_time
                    predecessors[neighbor] = src
                    print(predecessors)

        visited.add(src)
        unvisited=[]
        
        for k in graph:
            if k not in visited:
                heappush(unvisited, (times.get(k, float('inf')), k))   

        nodo_actual = heappop(unvisited)[1] 
        return dijkstra_tiempo(graph, nodo_actual, dest, mes, hora, minutos, visited, times, predecessors)  

In [86]:
def vecino_cercano(graph, nodes, src, dest, mes, hora, minutos, new_time = 0, visited={}, historico={}, betados=set(), predecessors={}):
    visited.add(src)
    """ calculates a shortest path tree routed in src
    """    
    if src == dest:
        #print('LLEGÓ AL DESTINO------------------')
        # We build the shortest path and display it
        path=[]
        pred=dest
        while pred != None:
            path.append(pred)
            pred=predecessors.get(pred,None)
        # reverses the array, to display the path nicely
        readable = path[0]

        return(path, new_time)
        
    else : 
            
        neighbor_list = []
        neighbor_times = []
        neighbor_times_prob = []
        
        for neighbor in graph[src] :
            #vecinos_v = list(graph[neighbor].keys())
            #print('vecinos_v', vecinos_v)
            #for v in vecinos_v:
            #    if v in visited:
            #        vecinos_v.remove(v)
            #        print('vecinos_v modificado, se le borraron vecinos', vecinos_v)
            if neighbor not in visited and neighbor not in betados and nx.has_path(graph, neighbor,dest):
                neighbor_list.append(neighbor)
                x = graph[src][neighbor][0]['speed_kph']
                if type(x) == list:
                    x = sum(x)
                y = graph[src][neighbor][0]['length']
                if type(y) == list:
                    y = sum(y)
                
                act_time = actualizar_tiempo(x, y, mes, hora, minutos)
                neighbor_times.append(act_time)
                
           
        
        
        
            prob = {}
            for n in range(len(neighbor_times)):
                # agregar a prob
                radio_dest = ox.distance.great_circle_vec(nodes[nodes['osmid'] == neighbor_list[n]]['y'].values[0], 
                                                          nodes[nodes['osmid'] == neighbor_list[n]]['x'].values[0], 
                                                          nodes[nodes['osmid'] == dest]['y'].values[0], 
                                                          nodes[nodes['osmid'] == dest]['x'].values[0], earth_radius = 6371009)
                prob[neighbor_list[n]] = radio_dest
            
            
                
        print('vecinos', neighbor_list) 
        print('tiempos', neighbor_times) 
        #SE OBTIENE OTRO MÍNIMO, YA QUE EL VECINO MÍNIMO YA FUE VISITADO PERO EL RESTO NO
        siguiente = src
        vv_visitados = True
        
        if len(neighbor_list) > 0:
            prob_values = list(prob.values())
            print('prob_values', prob_values)
            min_value = min(prob_values)
            max_value = max(prob_values)
             
                                                                
            # Aqui estamos actualizando la lista multiplicada por prob, dde revisaremos cercanía al dest
            for n in prob.values():
                if n == min_value: # el más cerca del destino
                    neighbor_times_prob.append(prob_values[prob_values.index(n)] * 0.1)
                elif n == max_value: # el más cerca del destino
                    neighbor_times_prob.append(prob_values[prob_values.index(n)] * 0.5)
                else:
                    neighbor_times_prob.append(prob_values[prob_values.index(n)] * 0.4)
                    
        while len(neighbor_list) > 0 and vv_visitados: 
            print('Entró al bucle con la neighbor_list', neighbor_list)
            indice_min = neighbor_times_prob.index(min(neighbor_times_prob))
            siguiente = neighbor_list[indice_min] # elige siguiente
            print('siguiente sería', siguiente)
            if siguiente in visited:
                print(siguiente, 'ya fue visitado')
                # Se borra de las posibilidades
                neighbor_times_prob.remove(neighbor_times_prob[neighbor_list.index(siguiente)])
                neighbor_times.remove(neighbor_times[neighbor_list.index(siguiente)])
                neighbor_list.remove(siguiente)
                print('neighbor_times y neighbor_list sin', siguiente, 'quedan como')
                print('neighbor_times_prob', neighbor_times_prob)
                print(neighbor_list)
            else:
                print(siguiente, 'no ha sido visitado, se debería salir del bucle')
                vv_visitados = False
                
            #Revisar la lisa de vecinos nueva: Sí aún tiene vecinos repetir lo anterior, sino se devuelve
        print('Si estaba en un bucle, salió')    
        #SE DEVUELVE SI --> No tiene vecinos    
        if len(neighbor_list) == 0:
            #predecessors buscar el elemento que tiene el value  de siguiente y borrarlo (se agrega al set betados),
            #antes borrarlo guardar su key como siguiente
            #dehacer último paso
            betados.add(siguiente)
            print('Se beto a', siguiente)
            siguiente = [predecessors.pop(key) for key in [siguiente]][0]
            print('ruta, dado que se borró un paso', predecessors)
            old_time = historico[siguiente]['tiempo_arco']
            mes = historico[siguiente]['mes']
            hora = historico[siguiente]['hora']
            minutos= historico[siguiente]['minutos']
            new_time = new_time - old_time
        else:
            
            print(src, 'Tiene vecinos decentes y siguiente es', siguiente)
            new_time = new_time + neighbor_times[indice_min]
            predecessors[siguiente] = src
            print('ruta', predecessors)
            historico[src] = {'dest':siguiente, 'mes':mes, 'hora': hora, 'minutos':minutos, 'tiempo_arco': neighbor_times[indice_min]}
            visited.add(siguiente)
            print('visitados', visited)
        
        
        return vecino_cercano(graph, nodes, siguiente, dest, mes, hora, minutos, new_time, visited, historico, betados, predecessors)

In [16]:
ejemplito = {4:3,3:2,2:1}
# 4 no tiene vecinos
siguiente = 3
print([ejemplito.pop(key) for key in [siguiente]])
ejemplito

[2]


{4: 3, 2: 1}

In [84]:
graph[1882519124]
nx.has_path(graph, 1882519124, 1552735798)

True

In [ ]:
grafi = subgrafo(graph, 4441341769, direccion_x, direccion_y, 2, 5)
a = vecino_cercano(grafi, nodes, 4441341769, 1552735798, 7, 6, 30, 0, set(), {}, set(), {})
a

vecinos [4441341770, 4441341778, 528021306]
tiempos [0.00016098280098280097, 0.0002707371007371007, 0.006915066666666666]
prob_values [32378.955070827706, 32375.38480123844, 31983.795746344043]
Entró al bucle con la neighbor_list [4441341770, 4441341778, 528021306]
siguiente sería 528021306
528021306 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
4441341769 Tiene vecinos decentes y siguiente es 528021306
ruta {528021306: 4441341769}
visitados {4441341769, 528021306}
vecinos [4441341779, 710772898, 539055230]
tiempos [0.00018330024813895782, 0.00030233250620347393, 0.0008674833333333333]
prob_values [31985.77469711818, 31979.923662812413, 31934.592817988756]
Entró al bucle con la neighbor_list [4441341779, 710772898, 539055230]
siguiente sería 539055230
539055230 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
528021306 Tiene vecinos decentes y siguiente es 539055230
ruta {528021306: 4441341769, 539055230: 528021306}
visitados {

vecinos [528105853]
tiempos [0.0010563166666666666]
prob_values [31028.891198283145]
Entró al bucle con la neighbor_list [528105853]
siguiente sería 528105853
528105853 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
6058312551 Tiene vecinos decentes y siguiente es 528105853
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551}
visitados {605150242, 605150243, 528105794, 6058312551, 4441341769, 528012393, 528105737, 2365565662, 528105712, 4441341780, 528105816, 528021306, 5516897372, 528105853, 539055230}
vecinos [4441345960, 710753842, 528105925]
tiempos [7.735042735042735e-05, 0.00027183760683760684, 0.0020546333333333337]
prob_values [31029.837390505352, 31025.590738996467, 30910.2688807104

vecinos [6023030562, 710751535]
tiempos [0.0007802166666666667, 0.0002040952380952381]
prob_values [30340.48712718079, 30383.5156880809]
Entró al bucle con la neighbor_list [6023030562, 710751535]
siguiente sería 6023030562
6023030562 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
583283021 Tiene vecinos decentes y siguiente es 6023030562
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021}
visitados {528105737, 4767926418, 605150242, 605150243, 6023030562, 528105773, 4441345967, 528021306,

vecinos [157332218]
tiempos [0.004133683333333333]
prob_values [29483.049876895406]
Entró al bucle con la neighbor_list [157332218]
siguiente sería 157332218
157332218 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
6058312553 Tiene vecinos decentes y siguiente es 157332218
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553}
visit

vecinos [2365558434]
tiempos [0.00016235]
prob_values [28673.77312588601]
Entró al bucle con la neighbor_list [2365558434]
siguiente sería 2365558434
2365558434 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
6061130691 Tiene vecinos decentes y siguiente es 2365558434
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553, 4504379924:

...

vecinos [3306878582]
tiempos [0.0004871333333333333]
prob_values [12224.55538690632]
Entró al bucle con la neighbor_list [3306878582]
siguiente sería 3306878582
3306878582 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
3306878505 Tiene vecinos decentes y siguiente es 3306878582
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553, 

vecinos [3306878489]
tiempos [0.0005422333333333333]
prob_values [12182.508955790496]
Entró al bucle con la neighbor_list [3306878489]
siguiente sería 3306878489
3306878489 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
3306878573 Tiene vecinos decentes y siguiente es 3306878489
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553,

vecinos [3306878429]
tiempos [0.0006481333333333333]
prob_values [12111.434471495304]
Entró al bucle con la neighbor_list [3306878429]
siguiente sería 3306878429
3306878429 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
3306878372 Tiene vecinos decentes y siguiente es 3306878429
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553,

vecinos [3306878459]
tiempos [0.0004455666666666667]
prob_values [12060.407632364326]
Entró al bucle con la neighbor_list [3306878459]
siguiente sería 3306878459
3306878459 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
3306878513 Tiene vecinos decentes y siguiente es 3306878459
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553,

vecinos [3306878492]
tiempos [0.0005188666666666666]
prob_values [11981.201984953464]
Entró al bucle con la neighbor_list [3306878492]
siguiente sería 3306878492
3306878492 no ha sido visitado, se debería salir del bucle
Si estaba en un bucle, salió
3306878387 Tiene vecinos decentes y siguiente es 3306878492
ruta {528021306: 4441341769, 539055230: 528021306, 5516897372: 539055230, 4441341780: 5516897372, 2365565662: 4441341780, 528012393: 2365565662, 528105737: 528012393, 528105816: 528105737, 605150243: 528105816, 605150242: 605150243, 528105712: 605150242, 528105794: 528105712, 6058312551: 528105794, 528105853: 6058312551, 528105925: 528105853, 528105773: 528105925, 4767926418: 528105773, 4441345967: 4767926418, 504604602: 4441345967, 3398930002: 504604602, 583283020: 3398930002, 583283021: 583283020, 6023030562: 583283021, 6023030560: 6023030562, 4441350600: 6023030560, 504639103: 4441350600, 6058312552: 504639103, 157340799: 6058312552, 6058312553: 157340799, 157332218: 6058312553,

In [ ]:
#predecessors = {1882519126: 1882519127, 1882519128: 1882519126, 1882519161: 1882519128, 6055795750: 1882519161, 6055795751: 6055795750, 6055795753: 6055795751, 990525992: 6055795753, 280839665: 990525992, 7140029037: 280839665, 6050190163: 7140029037, 280841556: 6050190163, 4431541904: 280841556, 280841591: 4431541904, 280841163: 280841591, 4431541896: 280841163, 4431520152: 4431541896, 280839664: 4431520152, 280839907: 280839664, 4431607727: 280839907, 280840540: 4431607727, 4431666676: 280840540, 4431666677: 4431666676, 280840539: 4431666677, 280839450: 280840539, 4431607728: 280839450, 280840223: 4431607728, 6050190151: 280840223, 4431520153: 6050190151, 4431541897: 4431520153, 280841164: 4431541897, 4431541905: 280841164, 280841555: 4431541905, 458570267: 280841555, 280839447: 458570267, 2362939162: 280839447, 6055952572: 2362939162, 4444821375: 6055952572, 6049951446: 4444821375, 6055947263: 6049951446, 6548809042: 6055947263, 6055947264: 6548809042, 6055947265: 6055947264, 6548809043: 6055947265, 6548809044: 6548809043, 5569835093: 6548809044, 6548809045: 5569835093, 6548809046: 6548809045, 5569835092: 6548809046, 990526001: 5569835092, 458570301: 990526001, 5569835082: 458570301, 6548809057: 5569835082, 6548809035: 6548809057, 1386670899: 6548809035, 6548809060: 1386670899, 6548809061: 6548809060, 6548809062: 6548809061, 6548809063: 6548809062, 6548809064: 6548809063, 4431703608: 6548809064, 280838628: 4431703608, 3997569493: 280838628, 3997569487: 3997569493, 6548809030: 3997569487, 605196534: 6548809030, 6050076401: 605196534, 277064464: 6050076401, 6055580045: 277064464, 4780124963: 6055580045, 6050076393: 4780124963, 6050076388: 6050076393, 4780124965: 6050076388, 6621324923: 4780124965, 6050069780: 6621324923, 6122244985: 6050069780, 6122216584: 6122244985, 6122216583: 6122216584, 6548809059: 6122216583, 6122216582: 6548809059, 6122216581: 6122216582, 6122216578: 6122216581, 6548809041: 6122216578, 5568246658: 6548809041, 6548809040: 5568246658, 5569835087: 6548809040, 6548809037: 5569835087, 6548809036: 6548809037, 990526167: 6548809036, 5569835091: 990526167, 5569835090: 5569835091, 458570662: 5569835090, 1882519182: 458570662, 6050184488: 1882519182, 6050182984: 6050184488, 6050184485: 6050182984, 6548809032: 6050184485, 6050184486: 6548809032, 6548809031: 6050184486, 6050184487: 6548809031, 6050182983: 6050184487, 6050182970: 6050182983, 5569835088: 6050182970, 6050182975: 5569835088, 6050182982: 6050182975, 5780599988: 6050182982, 5568247337: 5780599988, 1882519130: 5568247337, 6055795754: 1882519130, 1882519141: 6055795754, 6055795752: 1882519141, 1882519122: 6055795752, 1882519178: 1882519122, 5131231492: 1882519178, 6050270632: 5131231492, 1882519123: 6050270632, 6050270642: 1882519123, 6050270637: 6050270642, 6050270626: 6050270637, 6050270621: 6050270626, 5780599878: 6050270621, 1882519124: 5780599878, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 6932357774: 4431755693, 6932357775: 6932357774, 1882519165: 6932357775, 6055795740: 1882519165, 1882519145: 6055795740, 458570665: 1882519145, 5780599923: 458570665, 6055812421: 5780599923, 458570587: 6055812421, 5780599929: 458570587, 5780599897: 5780599929, 6050184533: 5780599897, 6050184534: 6050184533, 6050184542: 6050184534, 6050184548: 6050184542, 6050184543: 6050184548, 5780599895: 6050184543, 5780599947: 5780599895, 458570569: 5780599947, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 6050270477: 458570572, 6050270586: 6050270477, 4432880820: 6050270586, 6055793182: 4432880820, 6050139810: 6055793182, 6050139813: 6050139810, 4431741701: 6050139813, 5780600116: 4431741701, 458570932: 5780600116, 8578509528: 458570932, 5568246659: 8578509528, 3061219268: 5568246659, 3061219250: 3061219268, 458570774: 3061219250, 4444821371: 458570774, 4571996407: 4444821371, 458570521: 4571996407, 458570293: 458570521, 4504427690: 458570293, 4444821374: 4504427690, 1795173210: 4444821374, 1795173196: 1795173210, 1795173214: 1795173196, 6049951388: 1795173214, 458570637: 6049951388, 6049951385: 458570637, 6049948872: 6049951385, 6049948878: 6049948872, 458570448: 6049948878, 458570596: 458570448, 1249546612: 458570596, 6049913347: 1249546612, 4792010268: 6049913347, 280841168: 4792010268, 280841167: 280841168, 4431541898: 280841167, 280840205: 4431541898, 4431607729: 280840205, 280840782: 4431607729, 4431666678: 280840782, 4431666679: 4431666678, 280840781: 4431666679, 4431607730: 280840781, 280839900: 4431607730, 6049913351: 280839900, 4431541899: 6049913351, 4792010270: 4431541899, 4431607731: 4792010270, 4431607732: 4431607731, 6049913327: 4431607732, 458570605: 6049913327, 6049965406: 458570605, 6049913321: 6049965406, 6049951468: 6049913321, 4791987179: 6049951468, 4791987177: 4791987179, 280840815: 4791987177, 6055580020: 280840815, 6055580029: 6055580020, 5330234239: 6055580029, 472559132: 5330234239, 472559317: 472559132, 1249546604: 472559317, 472559318: 1249546604, 472559321: 472559318, 472559324: 472559321, 1249546605: 472559324, 1249546606: 1249546605, 5285073203: 1249546606, 5285073191: 5285073203, 267451167: 5285073191, 267450413: 267451167, 472553406: 267450413, 3997962448: 472553406, 3997962438: 3997962448, 4780169941: 3997962438, 267451164: 4780169941, 267451163: 267451164, 267451091: 267451163, 3997948713: 267451091, 1575110770: 3997948713, 1575110751: 1575110770, 472557180: 1575110751, 472557193: 472557180, 472557183: 472557193, 1575112087: 472557183, 3997977058: 1575112087, 1575112093: 3997977058, 3997976231: 1575112093, 1575110680: 3997976231, 1575110681: 1575110680, 1575110761: 1575110681, 5131231493: 1575110761, 1575110687: 5131231493, 3997962399: 1575110687, 1842158484: 3997962399, 2513435682: 1842158484, 4435216974: 2513435682, 3995402770: 4435216974, 3995402771: 3995402770, 3995402607: 3995402771, 3995402602: 3995402607, 7567232127: 3995402602, 3995402604: 7567232127, 3995402605: 3995402604, 3995402613: 3995402605, 3995402611: 3995402613, 3995402762: 3995402611, 4788842045: 3995402762, 3995402608: 4788842045, 3995402648: 3995402608, 3995402626: 3995402648, 3995402656: 3995402626, 1552735798: 3995402656}
path = a[0]

#pred = 1552735798
#while pred != None:
#    path.append(pred)
 #   pred=predecessors.get(pred,None)
# reverses the array, to display the path nicely
readable = path[0]
path = path[::-1]

fig, ax = ox.plot_graph_route(grafi, path, show = False, close = False)
ax.scatter(direccion_y[list_id.index(1552735798)], direccion_x[list_id.index(1552735798)], c='yellow')
plt.show()

In [ ]:
predecessors = {1882519124: 1882519127, 6050270608: 1882519124, 6050270607: 6050270608, 6055795762: 6050270607, 277063741: 6055795762, 6055795755: 277063741, 3997800578: 6055795755, 277063742: 3997800578, 277063743: 277063742, 5131231491: 277063743, 277063744: 5131231491, 4431755693: 277063744, 458570684: 4431755693, 277063745: 458570684, 277063746: 277063745, 1956066936: 277063746, 277063747: 1956066936, 1956066928: 277063747, 6055795763: 1956066928, 277063748: 6055795763, 458570583: 277063748, 5780600007: 458570583, 5780599896: 5780600007, 5780600073: 5780599896, 458570586: 5780600073, 5780600071: 458570586, 5780599954: 5780600071, 458570655: 5780599954, 6932357774: 458570655, 6932357775: 6932357774, 458570568: 6932357775, 5780599953: 458570568, 5780600072: 5780599953, 458570569: 5780600072, 5780600048: 458570569, 5780599911: 5780600048, 5780599909: 5780599911, 458570572: 5780599909, 458570542: 458570572, 5780600037: 458570542, 3454354451: 5780600037, 3454354450: 3454354451, 5780599912: 3454354450, 5780600036: 5780599912, 458570546: 5780600036, 5780599907: 458570546, 4431741708: 5780599907, 3035244389: 4431741708, 4379802867: 3035244389, 1790882954: 4379802867, 4431741709: 1790882954, 4788544995: 4431741709, 6932422700: 4788544995, 6932422697: 6932422700, 6932422696: 6932422697, 6932422695: 6932422696, 6932422699: 6932422695, 6932422694: 6932422699, 6932422693: 6932422694, 6932422698: 6932422693, 4431741712: 6932422698, 4379802858: 4431741712, 4379802860: 4379802858, 6055795692: 4379802860, 6055795687: 6055795692, 4379802866: 6055795687, 6055795697: 4379802866, 4431741705: 6055795697, 6932422692: 4431741705, 6932422691: 6932422692, 4431741707: 6932422691}
path=[]
pred = 6932422691
while pred != None:
    path.append(pred)
    pred=predecessors.get(pred,None)
# reverses the array, to display the path nicely
readable = path[0]
print(path[::-1])

In [ ]:
path = [1882519127, 1882519124, 6050270608, 6050270607, 6055795762, 277063741, 6055795755, 3997800578, 277063742, 277063743, 5131231491, 277063744, 4431755693, 458570684, 277063745, 277063746, 1956066936, 277063747, 1956066928, 6055795763, 277063748, 458570583, 5780600007, 5780599896, 5780600073, 458570586, 5780600071, 5780599954, 458570655, 6932357774, 6932357775, 458570568, 5780599953, 5780600072, 458570569, 5780600048, 5780599911, 5780599909, 458570572, 458570542, 5780600037, 3454354451, 3454354450, 5780599912, 5780600036, 458570546, 5780599907, 4431741708, 3035244389, 4379802867, 1790882954, 4431741709, 4788544995, 6932422700, 6932422697, 6932422696, 6932422695, 6932422699, 6932422694, 6932422693, 6932422698, 4431741712, 4379802858, 4379802860, 6055795692, 6055795687, 4379802866, 6055795697, 4431741705, 6932422692, 6932422691]
fig, ax = ox.plot_graph_route(grafi, path)

In [ ]:
grafi[6932422690]

In [ ]:
graph[6932422691]

In [ ]:
def subgrafoX(graph, src, dest, k):
    k_rutas = ox.distance.k_shortest_paths(graph, src, dest, k, weight='Tiempos de Viaje')
    lista_sets = []
    for counter, path in enumerate(k_rutas):
        lista_sets.append(set(path))
        if counter == k-1:
             break
    nodos = list(reduce(operator.or_, lista_sets))
    subgrafo = graph.subgraph(nodos)
    return subgrafo

**Actualizamos valores de arcos en el grafo de santiago, ahora se llamará G contiene velocidad con congestión**

In [ ]:
# G  = ox.utils_graph.graph_from_gdfs(nodes , edges , graph_attrs = None)

In [ ]:
# nodesG, edgesG = ox.graph_to_gdfs(G)

**Ahora podemos calcular la ruta mínima entre dos nodos, bajo cualquier atributo de arco**

In [18]:
nodos = pd.read_csv("coord_cercanos.csv")

In [19]:
list_id = []
for row in nodos.iterrows():
    list_id.append(row[1][3])
    
list_id


[1882519127,
 265690338,
 4441341769,
 504500120,
 376264329,
 1552735798,
 1260237000,
 6104118724,
 539055189,
 7418381958,
 1882519126,
 280840543]

In [20]:
ClientesAprox = pd.read_csv("coord_cercanos.csv")
direccion_x =[]
direccion_y =[]
for row in ClientesAprox.iterrows():
    direccion_x.append(row[1][1])
    direccion_y.append(row[1][2])

**Función que debe ir calculando los costos que difieren del tiempo**

(1286.7*(edges[lenght]/1000)) ---------------> Todos los arcos

(sumar + 21378) -----------------------------> Arcos salientes del depot

In [ ]:
def costos_agregados(path):
    agregados = 0
    for n in range(len(path)-1):
        if path[len(path)-1] == 267454352 and agregados == 0:
            agregados += 21378
        else:
            agregados += (1286.7 * graph[path[n+1]][path[n]][0]['length'])/1000
    return (agregados)

In [ ]:
# Calculate the shortest path dinamic time
def rutas_min_pares(G, list_id, mes, hora, minutos):
    tiempo_inicial = time() 
    dic_rutas = {}
    #G = ox.utils_graph.graph_from_gdfs(nodes , edges , graph_attrs = None)
    visitados = set()
    subgrafos = {}
    for n1 in list_id:
        for n2 in list_id:
            if n1 != n2 and nx.has_path(G, n1,n2):
                if (n1, n2) not in visitados:
                    subg = subgrafo(G, n1, direccion_x, direccion_y, list_id.index(n1), list_id.index(n2))
                    subgrafos[(n2, n1)] = subg
                    visitados.add((n2, n1))
                else:
                    subg = subgrafos[(n2, n1)]
                path, tiempo = dijkstra_tiempo(subg, n1, n2, mes, hora, minutos,set(), {}, {})
                print('-------------------------------------------------------------------------------------------------------------------------------------------------')
                print('Encontro ruta min con Dijsktra del par de nodos', (n1, n2))
                print('-------------------------------------------------------------------------------------------------------------------------------------------------')
                costo_agregado = costos_agregados(path)
                dic_rutas[(path[0], path[-1])] = [tiempo, costo_agregado]           
    tiempo_final = time() 
    tiempo_ejecucion = tiempo_final - tiempo_inicial
    print ('El tiempo de ejecucion en minutos fue:', tiempo_ejecucion/60)
    return(dic_rutas)

In [ ]:
dic_rutas = (rutas_min_pares(G, list_id, 6, 9, 0))

In [ ]:
print(dic_rutas)

Notamos que al ocupar el método 'haversine' se repite un nodo, debido a la cercania. De modo que dejaremos ese nodo con su id euclidiano.

**Revisamos todos los pares de nodos que efectivamente no tienen ruta entre sí**

In [ ]:
pares_sin_ruta = []
for n1 in list_id:
        for n2 in list_id:
            if n1 != n2 and nx.has_path(G, n1, n2)==False:
                pares_sin_ruta.append((n1, n2))
                
print('Los siguientes pares no tienen rutas entre sí:', pares_sin_ruta)

Hay 11 pares sin ruta entre sí

In [ ]:
len(pares_sin_ruta)

In [ ]:
diccionario_nodos = {}
list_id = []
i = 0
for row in nodos.iterrows():
    list_id.append(row[1][3])
    diccionario_nodos[row[1][3]] = i
    i+=1
print(diccionario_nodos)

No están existiendo conexiones salientes de los nodos 0, 2 y 3.

In [ ]:
pares = []
for par in pares_sin_ruta:
    pares.append((diccionario_nodos[par[0]],diccionario_nodos[par[1]]))
print(pares)    

In [ ]:
list_id = [1882519127, 265690338, 4441341769]
tamaños = []
subgrafos = {}
for i in list_id:
    for j in list_id: 
        if i != j:
            grafito = subgrafo(graph, i, direccion_x, direccion_y, list_id.index(i), list_id.index(j))
            tamaños.append(len(grafito.nodes))
            subgrafos[(i, j)] = grafito
            if j not in grafito:
                print(diccionario_nodos[j],' no está en el subgrafo generado desde', diccionario_nodos[i])

In [ ]:
print(subgrafos)

In [ ]:
print(max(tamaños))

In [ ]:
print(direccion_y)

In [ ]:
prueba = ox.distance.great_circle_vec(direccion_x[5], direccion_y[5], direccion_x[8], direccion_y[8], earth_radius = 6371009)
print(prueba/100)

In [ ]:
len(grafito.nodes)

In [ ]:
247688-219954


# -----------------------------------------------------------------------------------------------------

In [ ]:
"""# Necesitamos ahora, crear la estructura de grafo sin calles con los costos reales en los arcos entre cada par o-d
#Se importa la libreria networkx como nx

import networkx as nx

#Se importa la libreria pyplot de matplotlib como plt

import matplotlib.pyplot as plt

#Se crea un grafo asimétrico vacio

G = nx.DiGraph()

#Se crean los nodos:

#Se crean los nodos depot + clientes

G.add_nodes_from(list_id)

#Se crean los arcos entre los nodos
for a in dic_rutas:
    G.add_edge(a[0], a[1])
    G.edges[(a[0], a[1])]['Costo']= dic_rutas[a]
for n in G.nodes:
    if n == 267454352:
        G.nodes[n]['Depot'] = True
    else:
        G.nodes[n]['Depot'] = False
    
#Se dibuja el grafo

nx.draw(G, node_size = 12, font_size=1)

#Se muestra en pantalla

plt.show()"""



In [ ]:
"""G.nodes"""

In [ ]:
"""G.edges"""

In [ ]:
"""G.edges[(3485642555, 4765300244)]"""

In [ ]:
"""G.nodes[613890784]"""

# Creación de datos

In [ ]:
"""n = list_id.copy()# Clientes
camiones = [k for k in range (1,4)]
list_id.remove(267454352)
clientes = list_id
u={1: 5500, 2:5500, 3:5500}

import numpy as np
rnd=np.random
rnd.seed(0)

q={i:rnd.randint(500, 1000) for i in clientes}"""

In [ ]:
"""print(n)
print(clientes)
print(camiones)
print(u)
print(q)
print(list_id)"""

In [ ]:
"""import matplotlib.pyplot as plt

plt.figure(figsize=(12,5))
plt.scatter(direccion_x,direccion_y,color="green")

for i in clientes:
       plt.annotate('$q_{%d}=%d$'%(i,q[i]),(direccion_x[clientes.index(i)],direccion_y[clientes.index(i)]))
    
plt.plot(direccion_x[0],direccion_y[0],color='red',marker='s')
plt.annotate('DC',(direccion_x[0],direccion_y[0]))

plt.xlabel("Eje X")
plt.ylabel("Eje Y")
plt.title("Gráfico de Nodos | VRP")

plt.show()"""



In [ ]:
"dic_rutas[(3485642555, 4765300244)]"

In [ ]:
""""arcos={i for i in dic_rutas.keys()}
# esto es literal dic_rutas
#distancia={(i,j):np.hypot(direccion_x[i]-direccion_x[j],direccion_y[i]-direccion_y[j]) 
          # for i in nodos for j in nodos if i!=j}
arcos"""

In [ ]:
"""plt.figure(figsize=(12,5))
plt.scatter(direccion_x,direccion_y,color="green")

for i in clientes:
    plt.annotate('$q_{%d}$'%(i),(direccion_x[clientes.index(i)],direccion_y[clientes.index(i)]))
    
plt.plot(direccion_x[0],direccion_y[0],color='red',marker='s')
plt.annotate('DC',(direccion_x[0],direccion_y[0]))

for i, j in arcos:
    plt.plot([direccion_x[n.index(i)],direccion_x[n.index(j)]],[direccion_y[n.index(i)],direccion_y[n.index(j)]],color="blue",alpha=0.3)
    #plt.annotate('C=%d'%dic_rutas[(i,j)], ((direccion_x[n.index(i)]+direccion_x[n.index(j)])/2, (direccion_y[n.index(i)]+direccion_y[n.index(j)])/2))
plt.xlabel("Eje X")
plt.ylabel("Eje Y")
plt.title("Grafo completo, arcos entre todo par de nodos donde existe ruta| VRP")


plt.show()"""

Fuente: https://nbviewer.jupyter.org/github/CplexPython/Cplex-Python/blob/master/VRP/CVRP%20%7C%20Cplex%20%26%20Python%20.ipynb

# Utilizando Heurísticas para resolver VRP

In [ ]:
"""# Plot the shortest path
fig, ax = ox.plot_graph_route(G, route)"""